In [1]:
import pandas as pd
from chroma_db import ChromaDB

In [4]:
data = pd.read_csv('Corpus_v4.csv')
data.head()

link  \
0  https://cbr.ru//support_measures/   
1  https://cbr.ru//support_measures/   
2         https://cbr.ru//reception/   
3         https://cbr.ru//reception/   
4  https://cbr.ru//support_measures/   

                                                text  pages  is_markdown  
0  Меры защиты финансового рынка Банк России прин...    NaN        False  
1  Меры защиты финансового рынка Банк России прин...    NaN        False  
2  Интернет-приемная Хотите обратиться в Банк Рос...    NaN        False  
3  Интернет-приемная Хотите обратиться в Банк Рос...    NaN        False  
4  Меры защиты финансового рынка Банк России прин...    NaN        False

In [50]:
import nltk
from nltk.tokenize import word_tokenize, sent_tokenize

nltk.download('punkt')

c:\ProgramData\Anaconda3\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Никита\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [6]:
def get_nltk_chunks(text, chunk_size=200, chunk_overlap=100, language="russian"):
    words = word_tokenize(text, language=language)

    chunks = []

    end_index = chunk_size
    while end_index - chunk_size < len(words):
        sentence = ''
        for word in words[end_index - chunk_size:end_index]:
            if word in ',.?!:)»' or (sentence and sentence[-1] in '«('):
                sentence += word
            else:
                sentence += " " + word

        chunks.append(sentence)
        end_index += chunk_size - chunk_overlap

    return chunks

In [17]:
# for chunk in get_nltk_chunks(data.text[319], chunk_size = 200, chunk_overlap = 20):
#     print(len(chunk), chunk)
#     print()

In [2]:
chroma = ChromaDB('84.201.178.246', port=8000)

In [3]:
res = chroma.select_all()

In [5]:
res.keys()

dict_keys(['ids', 'embeddings', 'metadatas', 'documents', 'data', 'uris'])

In [15]:
doc_lengths = pd.DataFrame(columns=['len', 'id'])

In [16]:
for i, doc, true_id in zip(range(len(res['documents'])), res['documents'], res['ids']):
    if i % 1_000 == 0:
        print(i)
    doc_lengths.loc[len(doc_lengths)] = [len(doc), true_id]

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000


In [46]:
doc_lengths[doc_lengths.len<707]

len     id
1       39      1
26     669   1002
37      22   1003
70       7   1006
115    155   1010
...    ...    ...
91700  113  v9976
91704  326   v998
91706  132  v9981
91713  105  v9988
91725  156  v9999

[22490 rows x 2 columns]

In [38]:
doc_lengths.len.describe()

count    91726.000000
mean       875.900464
std        444.551045
min          1.000000
25%        707.000000
50%        916.000000
75%       1098.000000
max      14379.000000
Name: len, dtype: float64

In [45]:
doc_lengths[doc_lengths.len<707].id.to_list()

['1',
 '1002',
 '1003',
 '1006',
 '1010',
 '1019',
 '1030',
 '1039',
 '1041',
 '1048',
 '1051',
 '1069',
 '1071',
 '1080',
 '1088',
 '109',
 '1092',
 '1113',
 '1115',
 '1129',
 '1130',
 '1134',
 '1147',
 '115',
 '1169',
 '1172',
 '11808',
 '11813',
 '1182',
 '11823',
 '1196',
 '12',
 '120',
 '1209',
 '1214',
 '1217',
 '1222',
 '1224',
 '1226',
 '1230',
 '1232',
 '1234',
 '1235',
 '1236',
 '1237',
 '1238',
 '1239',
 '1244',
 '1245',
 '1248',
 '1249',
 '125',
 '1250',
 '1251',
 '1252',
 '1253',
 '1254',
 '1265',
 '1272',
 '128',
 '1290',
 '1300',
 '1317',
 '1330',
 '134',
 '1346',
 '136',
 '1363',
 '1374',
 '1387',
 '139',
 '1401',
 '1414',
 '1427',
 '1440',
 '145',
 '1450',
 '1478',
 '1489',
 '1500',
 '1514',
 '1517',
 '1540',
 '1562',
 '1574',
 '1599',
 '160',
 '1623',
 '1633',
 '164',
 '16451',
 '16469',
 '16480',
 '16491',
 '16502',
 '16513',
 '16524',
 '16535',
 '16546',
 '16557',
 '16568',
 '16579',
 '1658',
 '16590',
 '16601',
 '16612',
 '16623',
 '16634',
 '16645',
 '16656',
 '16

In [53]:
doc_707 = pd.DataFrame(columns=['tokens', 'id'])
for i, doc, true_id in zip(range(len(res_small['documents'])), res_small['documents'], res_small['ids']):
    if i % 1_000 == 0:
        print(i)
    doc_707.loc[len(doc_707)] = [len(word_tokenize(doc)), true_id]

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000


In [79]:
doc_707[doc_707.tokens<60]

tokens     id
0           4      1
2           3   1003
3           1   1006
4          17   1010
5          35   1019
...       ...    ...
22483      44  v9967
22485      20  v9976
22487      19  v9981
22488      17  v9988
22489      30  v9999

[10206 rows x 2 columns]

In [85]:
res = chroma.select_all()
len(res['ids'])

81520

In [83]:
len(res['ids'])

91726

In [88]:
chroma.embedding_function.change_mode(new_mode='query')
knn_res = chroma.collection.query(
            query_texts=['где можно купить фирменные чеканные монеты'],
            n_results=50)

In [89]:
knn_res['documents']

[[', начиная с 2016 г. чеканки на аверсах всех монет, в оформлении которых использовалась эмблема Банка России, размещается изображение Государственного герба Российской Федерации. Также изображение Государственного герба Российской Федерации размещено на банкнотах Банка России образца 2017 г. и памятных банкнотах Банка России номиналом 100 рублей, посвященных Чемпионату мира по футболу FIFA 2018 года. 20 Вправе ли банки отказывать клиенту в размене наличных денег? Обновлено: 04.03.2020 В соответствии с Положением Банка России от 29.01.2018 № 630-П «О порядке ведения кассовых операций и правилах хранения, перевозки и инкассации банкнот и монеты Банка России в кредитных организациях на территории Российской Федерации» размен банкнот Банка России, монеты Банка России одного номинала на банкноты Банка России, монету Банка России другого номинала осуществляют кредитные организации (филиалы), их внутренние структурные подразделения, совершающие банковскую операцию по инкассации денежных сре

In [91]:
chroma.bm25_request('где можно купить фирменные чеканные монеты', n_results=50, chunk_window=3)

ValueError: Expected where value for $and or $or to be a list with at least two where expressions, got [{'chunk_id': 0}]

In [94]:
chroma.query_knn('где можно купить фирменные чеканные монеты', n_results=3, chunk_window = 6)

[{'ids': ['543', '544', '545', '546', '547'],
  'embeddings': None,
  'metadatas': [{'chunk_id': 8,
    'doc_id': 140,
    'is_markdown': False,
    'link': 'https://cbr.ru//faq/ndo/',
    'max_length': 14},
   {'chunk_id': 9,
    'doc_id': 140,
    'is_markdown': False,
    'link': 'https://cbr.ru//faq/ndo/',
    'max_length': 14},
   {'chunk_id': 10,
    'doc_id': 140,
    'is_markdown': False,
    'link': 'https://cbr.ru//faq/ndo/',
    'max_length': 14},
   {'chunk_id': 11,
    'doc_id': 140,
    'is_markdown': False,
    'link': 'https://cbr.ru//faq/ndo/',
    'max_length': 14},
   {'chunk_id': 12,
    'doc_id': 140,
    'is_markdown': False,
    'link': 'https://cbr.ru//faq/ndo/',
    'max_length': 14}],
  'documents': [' инвестиционные монеты на территории РФ? Обновлено: 16.12.2019 Банк России в соответствии со своим статусом не проводит операции с физическими лицами. По вопросам приобретения памятных и инвестиционных монет из драгоценных металлов, а также монет из недрагоценных

In [80]:
res_small = chroma.get_chunk_by_ids(doc_707[doc_707.tokens<60].id.to_list())

In [75]:
doc_707[doc_707.tokens<100].id.to_list()

['1',
 '1003',
 '1006',
 '1010',
 '1019',
 '1030',
 '1039',
 '1041',
 '1048',
 '1051',
 '1069',
 '1080',
 '109',
 '1092',
 '1113',
 '1115',
 '1129',
 '1130',
 '1134',
 '1147',
 '115',
 '1169',
 '11808',
 '11813',
 '1182',
 '1196',
 '12',
 '120',
 '1209',
 '1214',
 '1217',
 '1222',
 '1224',
 '1230',
 '1232',
 '1234',
 '1235',
 '1236',
 '1237',
 '1238',
 '1239',
 '1244',
 '1245',
 '1249',
 '1250',
 '1251',
 '1252',
 '1253',
 '1254',
 '1265',
 '1272',
 '128',
 '1300',
 '1330',
 '134',
 '1346',
 '136',
 '1363',
 '1374',
 '139',
 '1401',
 '1427',
 '145',
 '1450',
 '1478',
 '1489',
 '1500',
 '1514',
 '1517',
 '1540',
 '1562',
 '1574',
 '1599',
 '160',
 '1623',
 '1633',
 '164',
 '16469',
 '16480',
 '16491',
 '16502',
 '16513',
 '16524',
 '16535',
 '16546',
 '16557',
 '16568',
 '16579',
 '1658',
 '16590',
 '16601',
 '16612',
 '16623',
 '16634',
 '16645',
 '16656',
 '16667',
 '16678',
 '16681',
 '16683',
 '16694',
 '16705',
 '16716',
 '1672',
 '16727',
 '16738',
 '16749',
 '16760',
 '16771',
 '

In [81]:
res_small['documents']

[' условиях реализации санкционных рисков',
 ' 29 Сбросить Применить',
 ' ссылку',
 ' направленному против клиентов финансовых организаций. Руководство Директор департамента — В.А. Уваров Направление деятельности Информационная безопасность',
 ' рекомендации к действиям, обоснованные анализом несуществующих в действительности данных, расцениваются Банком России как недобросовестная практика, способная искажать ценообразование на финансовом рынке. Подробнее ... Ответственные структурные подразделения: Департамент инфраструктуры финансового рынка',
 ' практикам участников рынка 5 31.10.2018 Концепция противодействия недобросовестным действиям на финансовом рынке Противодействие недобросовестным практикам участников рынка Ответственное структурное подразделения: Департамент небанковского кредитования, Департамент инфраструктуры финансового рынка',
 ' договоров Методические рекомендации Банка России № 1-МР от 17.01.2023 Методические рекомендации по установлению критериев существенного откл

In [67]:
len(res["ids"])

91726

In [48]:
res_small['documents']

[' условиях реализации санкционных рисков',
 ' 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 < Пред След > Январь 2019 2020 2021 2022 2023 2024 Пн Вт Ср Чт Пт Сб Вс 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 Сбросить Применить Искать Выберите период За все время За все время Выбрать период ДД.ММ.ГГГГ - ДД.ММ.ГГГГ ДД.ММ.ГГГГ - ДД.ММ.ГГГГ < Пред След > Январь Февраль 2020 2021 2022 2023 2024 Пн Вт Ср Чт Пт Сб Вс 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 < Пред След > Январь Февраль 2020 2021 2022 2023 2024 Пн Вт Ср Чт Пт Сб Вс 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 Сбросить Применить',
 ' 29 Сбросить Применить',
 ' ссылку',
 ' направленному против клиентов финансовых организаций. Руководство Директор департамента — В.А. Уваров Направление деятельности Информационная безопасность',
 ' рекомендации к действиям, обоснованные анализом несуществующих в действительност

In [1]:
import logging

logging.basicConfig(level=logging.INFO, filename='db.log', filemode="a",
                       format="%(asctime)s %(levelname)s %(message)s")

In [20]:
for index, row in data[:10000].iterrows(): 
    try:
        if index % 25 == 0:
            logging.info(f'{index} done')
        link = row.link
        text = row.text
        pages = row.pages
        is_markdown = row.is_markdown
        if is_markdown:
            chunks = get_nltk_chunks(text, chunk_size = 2000, chunk_overlap = 100)
        else:
            chunks = get_nltk_chunks(text, chunk_size = 200, chunk_overlap = 20)
        chroma.insert_document(index, chunks, link, is_markdown, pages)
    except Exception as e:
        logging.error(index)

In [37]:
errors = []

with open('db.log') as f:
    for line in f.readlines():
        splitted = line.split()
        if len(splitted) > 2 and splitted[2] == 'ERROR':
                errors.append(int(splitted[3]))

In [69]:
print(errors)

[12, 13, 43, 47, 49, 62, 67, 87, 108, 162, 187, 203, 209, 219, 292, 302, 308, 312, 318, 319, 401, 404, 407, 419, 441, 459, 499, 542, 549, 582, 680, 717, 739, 812, 821, 839, 854, 872, 876, 879, 912, 941, 945, 994, 1008, 1011, 1024, 1044, 1045, 1051, 1077, 1081, 1082, 1084, 1114, 1115, 1135, 1157, 1175, 1212, 1753, 1758, 1823, 1863, 1875, 1926, 1928, 1929, 1930, 1931, 1936, 1940, 1941, 1959, 2103, 2105, 2112, 2113, 2114, 2115, 2116, 2117, 2118, 2119, 2120, 2121, 2122, 2123, 2124, 2125, 2126, 2127, 2128, 2129, 2130, 2131, 2132, 2133, 2134, 2135, 2136, 2137, 2138, 2139, 2221, 2228, 2229, 2230, 2231, 2232, 2233, 2234, 2235, 2236, 2237, 2238, 2239, 2246, 2248, 2249, 2251, 2252, 2255, 2256, 2258, 2260, 2275, 2280, 2294, 2304, 2319, 2377, 2386, 2391, 2406, 2428, 2442, 2443, 2446, 2473, 2516, 2583, 2677, 2678, 2682, 2691, 2719, 2724, 2725, 2726, 2729, 2773, 2774, 2818, 2820, 2852, 2892, 2893, 2907, 2909, 2910, 2911, 2912, 2914, 2918]


In [71]:
for index, row in data.iloc[errors].iterrows():
    if len(row.text) == float:
        print(row.text, index)

Вопросы и ответы Актуальные вопросы работы финансовой системы Разъяснения по специальным мерам защиты экономики Искать Все Новое Обновлено Меры поддержки мобилизованных и участников СВО Кредитные каникулы Золотовалютные резервы 1 Почему Банк России не хранил золотовалютные резервы внутри страны? Обновлено: 25.03.2022 Золотовалютные резервы — это инструмент, за счет которого центральный банк может защищать экономику от внешних кризисов. В тяжелых ситуациях они обеспечивают выплату валютного долга, критический импорт, стабилизируют валютный рынок. Хранить резервы внутри страны или потратить их внутри страны — это все равно что не иметь никаких резервов, вообще никакой защиты от внешних кризисов. Так наша страна жила в 1992–1999 годах. Тогда она была беззащитна перед внешними угрозами, это был практически непрекращающийся финансовый кризис. Именно поэтому центральный банк стремится накапливать резервы в хорошие времена и формировать структуру резервов таким образом, чтобы она позволила от

In [52]:
type(data.iloc[8586].text

' '

In [70]:
len(errors)

165